In [111]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.utils.data as data
import math
import copy

In [112]:
class MultiHeadAttention(nn.Module):
  def __init__(self,d_model,num_heads) -> None:
    super(MultiHeadAttention,self).__init__()
    self.d_model=d_model
    self.num_heads=num_heads
    self.d_k=self.d_model//self.num_heads

    self.W_q=nn.Linear(d_model,d_model)
    self.W_k=nn.Linear(d_model,d_model)
    self.W_v=nn.Linear(d_model,d_model)
    self.W_o=nn.Linear(d_model,d_model) #output
  def scaled_dot_product_attention(self,Q,K,V, mask=None):
    attn_scores=torch.matmul(Q,K.transpose(-2,-1))/math.sqrt(self.d_k)
    if mask is not None:
      attn_sores=attn_scores.masked_fill(mask==0,-1e9)
    attn_probs=torch.softmax(attn_scores, dim=-1)
    output=attn_probs@V
    return output
  def split_heads(self,x):
    batch_size,seq_len,d_model=x.size()
    return x.view(batch_size,seq_len,self.num_heads,self.d_k).transpose(1,2)
  def combine_heads(self,x):
    batch_size,_,seq_len,d_k=x.size()
    return x.transpose(1,2).contiguous().view(batch_size,seq_len,self.d_model)
  def forward(self,Q,K,V,mask=None):
    Q=self.split_heads(self.W_q(Q))
    K=self.split_heads(self.W_k(K))
    V=self.split_heads(self.W_v(V))
    attn_output = self.scaled_dot_product_attention(Q,K,V,mask=None)

    output=self.W_o(self.combine_heads(attn_output))
    return output



In [113]:
class PositionWiseFeedForward(nn.Module):
  def __init__(self,d_model,d_ff):
    super(PositionWiseFeedForward, self).__init__()
    self.fc_1=nn.Linear(d_model,d_ff)
    self.fc_2=nn.Linear(d_ff,d_model)
    self.relu=nn.ReLU().to(device)
  def forward(self,x):
    return self.fc_2(self.relu(self.fc_1(x)))




In [114]:
class PositionalEncoding(nn.Module):
  def __init__(self,d_model,max_seq_len) -> None:
    super(PositionalEncoding,self).__init__()
    pe=torch.zeros(max_seq_len,d_model).to(device)
    position=torch.arange(0,max_seq_len,dtype=torch.float).unsqueeze(1).to(device)
    # div_term = torch.exp(torch.arange(0,d_model,2)).float() *(-math.log(10000.0/d_model))
    div_term=torch.exp(torch.arange(0,d_model,2).float()*(-math.log(10000.0)/d_model)).to(device)
    pe[:,0::2]=torch.sin(position*div_term)
    pe[:,1::2]=torch.cos(position*div_term)
    self.register_buffer("pe",pe.unsqueeze(0))
  def forward(self,x):
    return x + self.pe[:,:x.size(1)]


In [115]:
class LayerNorma(nn.Module):

  def __init__(self,epsilon=0.1):
        super().__init__()
        self.eps=epsilon
        self.alpha=nn.Parameter(torch.ones(1)).to(device)
        self.bias=nn.Parameter(torch.zeros(1)).to(device)
  def forward(self,x):
        mean=x.mean(dim=-1,keepdim=True)
        std=x.std(dim=-1,keepdim=True)
        return self.alpha * (x-mean)/(std+self.eps)+self.bias

In [116]:

class EncoderLayer(nn.Module):
  def __init__(self,d_model,num_heads,d_ff,dropout):
    super(EncoderLayer,self).__init__()
    self.multihead=MultiHeadAttention(d_model,num_heads)
    self.feedforward=PositionWiseFeedForward(d_model,d_ff)
    self.norm1=nn.LayerNorm(d_model)
    self.norm2=nn.LayerNorm(d_model)
    # self.norm1=LayerNorma()
    # self.norm2=LayerNorma()
    self.dropout=nn.Dropout(dropout)

  def forward(self,x,mask):
    attn_output=self.multihead(x,x,x,mask)
    x=self.norm1(x+self.dropout(attn_output))
    ff_output=self.feedforward(x)
    x=self.norm2(x+self.dropout(ff_output))
    return x


In [117]:
class DecoderLayer(nn.Module):
  def __init__(self,d_model,num_heads,d_ff,dropout):
    super(DecoderLayer,self).__init__()
    self.selfattn=MultiHeadAttention(d_model,num_heads)
    self.crossattn=MultiHeadAttention(d_model,num_heads)
    self.feedforward=PositionWiseFeedForward(d_model,d_ff)
    self.norm1=nn.LayerNorm(d_model)
    self.norm2=nn.LayerNorm(d_model)
    self.norm3=nn.LayerNorm(d_model)
    # self.norm1=LayerNorma()
    # self.norm2=LayerNorma()
    # self.norm3=LayerNorma()
    self.dropout=nn.Dropout(dropout)
  def forward(self,x,enc_out,src_mask,tgt_mask):
    attn_output=self.selfattn(x,x,x,tgt_mask)
    x=self.norm1(x+self.dropout(attn_output))
    c_attn_out=self.crossattn(enc_out,enc_out,x,src_mask)
    x=self.norm2(x+self.dropout(c_attn_out))
    ff_out=self.feedforward(x)
    x=self.norm3(x+self.dropout(ff_out))
    return x

In [118]:

def causal_mask(size):
    mask=torch.triu(torch.ones(1,size,size),diagonal=1).type(torch.int)
    return mask==0

In [119]:
class Transformer(nn.Module):
  def __init__(self,src_vocab_size,tgt_vocab_size,d_model,num_heads,num_layers,d_ff,max_seq_len,dropout):
    super(Transformer,self).__init__()
    self.encoder_embedding=nn.Embedding(src_vocab_size,d_model)
    self.decoder_embedding=nn.Embedding(tgt_vocab_size,d_model)

    self.positional_encoding=PositionalEncoding(d_model,max_seq_len).to(device)
    self.encoder_layers=nn.ModuleList([EncoderLayer(d_model,num_heads,d_ff,dropout) for _ in  range(num_layers)])
    self.decoder_layers=nn.ModuleList([DecoderLayer(d_model,num_heads,d_ff,dropout) for _ in range(num_layers)])

    self.fc_layer=nn.Linear(d_model,tgt_vocab_size)
    self.dropout=nn.Dropout(dropout)

  def generate_mask(self,src,tgt):
    src_mask=(src!=1).unsqueeze(1).unsqueeze(2).to(device) # include padding seq are not involved
    tgt_mask=(tgt!=1).unsqueeze(1).unsqueeze(3).to(device) # include padding seq are not involved
    seq_length=tgt.size(1)
    nopeak_mask=(1- torch.triu(torch.ones(1, seq_length, seq_length), diagonal=1)).bool()
    tgt_mask=tgt_mask & nopeak_mask.to(device) # future tokens are not visible
    return src_mask.to(device),tgt_mask.to(device)
  def forward(self,src,tgt):
    src_mask,tgt_mask=self.generate_mask(src,tgt)
    # print("src",src_mask, "tgt",tgt_mask)
    src_embedded=self.dropout(self.positional_encoding(self.encoder_embedding(src))).to(device)
    # print(src_embedded)
    tgt_embedded=self.dropout(self.positional_encoding(self.decoder_embedding(tgt))).to(device)
    # print(tgt_embedded)
    enc_output=src_embedded
    for encoder_layer in self.encoder_layers:
      enc_output=encoder_layer(enc_output,src_mask).to(device)

    for decoder_layer in self.decoder_layers:
      dec_output=decoder_layer(tgt_embedded,enc_output,src_mask,tgt_mask).to(device)

    output=torch.log_softmax(self.fc_layer(dec_output),dim=-1).to(device)
    # print(output)

    return output


In [120]:
from datasets import load_dataset
from tokenizers import Tokenizer
from tokenizers.models import WordLevel
from tokenizers.trainers import WordLevelTrainer
from tokenizers.pre_tokenizers import Whitespace

# Pathlib?
from pathlib import Path

# typing
from typing import Any

# Library for progress bars in loops
from tqdm import tqdm

# Importing library of warnings
import warnings

In [121]:
import torch
import torch.nn as nn
from datasets import load_dataset
from torch.utils.data import Dataset, DataLoader, random_split
from tokenizers import Tokenizer
from tokenizers.models import WordLevel
from tokenizers.trainers import WordLevelTrainer
from tokenizers.pre_tokenizers import Whitespace

from pathlib import Path
import numpy as np

In [134]:
def get_all_sentences(ds,lang):
  for item in ds:
    yield item["translation"][lang]
def get_or_build_tokenizer(config,ds,lang):
  tokenizer_path=Path(config["tokenizer_file"].format(lang))
  if not Path.exists(tokenizer_path):
    tokenizer=Tokenizer(WordLevel(unk_token="[UNK]"))
    tokenizer.pre_tokenizer=Whitespace()
    trainer=WordLevelTrainer(special_tokens=["[UNK]","[PAD]","[SOS]","[EOS]"],min_frequency=2)
    tokenizer.train_from_iterator(get_all_sentences(ds,lang),trainer=trainer)
    tokenizer.save(str(tokenizer_path))
  else:
    tokenizer=Tokenizer.from_file(str(tokenizer_path))
  return tokenizer
def get_ds(config):
  ds_raw=load_dataset("opus_books", f'{config["lang_src"]}-{config["lang_tgt"]}', split="train")
  #build tokenizers
  def create_subset(dataset, sample_size):
    indices = np.random.choice(len(dataset), sample_size, replace=False)
    subset = dataset.select(indices)
    return subset
  # ds_raw=create_subset(ds_raw,10)

  tokenizer_src=get_or_build_tokenizer(config,ds_raw,config["lang_src"])
  tokenizer_tgt=get_or_build_tokenizer(config,ds_raw,config["lang_tgt"])

  train_ds_size = int(0.9*len(ds_raw))
  val_ds_size=len(ds_raw)-train_ds_size
  train_ds_raw,val_ds_raw=random_split(ds_raw,[train_ds_size,val_ds_size])

  train_ds= BilingualDataset(train_ds_raw, tokenizer_src,tokenizer_tgt,config["lang_src"],config["lang_tgt"],config["seq_len"])
  val_ds= BilingualDataset(train_ds_raw, tokenizer_src,tokenizer_tgt,config["lang_src"],config["lang_tgt"],config["seq_len"])

  max_len_src=0
  max_len_tgt=0

  for item in ds_raw:
    src_ids=tokenizer_src.encode(item["translation"][config["lang_src"]]).ids
    tgt_ids=tokenizer_tgt.encode(item["translation"][config["lang_src"]]).ids
    max_len_src=max(max_len_src,len(src_ids))
    max_len_tgt=max(max_len_src,len(src_ids))
  # print("max",max_len_src)
  # print("max",max_len_tgt)
  train_dataloader=DataLoader(train_ds,batch_size=config["batch_size"],shuffle=True)
  val_dataloader=DataLoader(val_ds,batch_size=1,shuffle=True)

  return train_dataloader, val_dataloader, tokenizer_src, tokenizer_tgt





In [135]:
class BilingualDataset(Dataset):
  def __init__(self,ds,tokenizer_src,tokenizer_tgt,src_lang,tgt_lang,seq_len):
    self.ds=ds
    self.tokenizer_src=tokenizer_src
    self.tokenizer_tgt=tokenizer_tgt
    self.src_lang=src_lang
    self.tgt_lang=tgt_lang
    self.seq_len=seq_len

    # self.sos_token=torch.tensor([tokenizer_src.token_to_id(["[SOS]"])],dtype=torch.int64)
    # self.eos_token=torch.tensor([tokenizer_src.token_to_id(["[EOS]"])],dtype=torch.int64)
    # self.pad_token=torch.tensor([tokenizer_src.token_to_id(["[PAD]"])],dtype=torch.int64)
    self.sos_token = torch.tensor([tokenizer_tgt.token_to_id("[SOS]")], dtype=torch.int64).to(device)
    self.eos_token = torch.tensor([tokenizer_tgt.token_to_id("[EOS]")], dtype=torch.int64).to(device)
    self.pad_token = torch.tensor([tokenizer_tgt.token_to_id("[PAD]")], dtype=torch.int64).to(device)

  def __len__(self):
    return len(self.ds)
  def __getitem__(self,index):
    src_target_pair=self.ds[index]
    src_text=src_target_pair["translation"][self.src_lang]
    tgt_text=src_target_pair["translation"][self.tgt_lang]

    enc_input_tokens=self.tokenizer_src.encode(src_text).ids
    dec_input_tokens=self.tokenizer_tgt.encode(tgt_text).ids

    enc_num_padding_tokens=self.seq_len-len(enc_input_tokens)-2
    dec_num_padding_tokens=self.seq_len-len(dec_input_tokens)-1

    if enc_num_padding_tokens<0 or dec_num_padding_tokens<0:
      raise ValueError("Sentence too long")


    # encoder_input=torch.cat([
    #     self.sos_token,
    #     torch.Tensor(enc_input_tokens,dtype=torch.int64),
    #     self.eos_token,
    #     torch.Tensor([self.pad_token]*enc_num_padding_tokens,dtype=torch.int64)
    # ])
    # decoder_input= torch.cat([
    #     self.sos_token,
    #     torch.Tensor(enc_input_tokens,dtype=torch.int64),
    #     torch.Tensor([self.pad_token]*dec_num_padding_tokens,dtype=torch.int64)
    # ])

    # label= torch.cat([
    #     torch.Tensor(dec_input_tokens,dtype=torch.int64),
    #     self.eos_token,
    #     torch.Tensor([self.pad_token]*dec_num_padding_tokens,dtype=torch.int64)
    # ])
    encoder_input =torch.cat(
            [
                self.sos_token,
                torch.tensor(enc_input_tokens,dtype=torch.int64).to(device),
                self.eos_token,
                torch.tensor([self.pad_token]*enc_num_padding_tokens,dtype=torch.int64).to(device)

            ]
        )

    decoder_input=torch.cat(
            [
                self.sos_token,
                torch.tensor(dec_input_tokens,dtype=torch.int64).to(device),
                torch.tensor([self.pad_token]*dec_num_padding_tokens,dtype=torch.int64).to(device)
            ]


        )

        # eos to label (what we expect output frm decoddeer)
    label=torch.cat(
            [   torch.tensor(dec_input_tokens,dtype=torch.int64).to(device),
                self.eos_token,
                torch.tensor([self.pad_token]*dec_num_padding_tokens,dtype=torch.int64).to(device)

            ]
        )
    assert encoder_input.size(0)== self.seq_len
    assert decoder_input.size(0)== self.seq_len
    assert label.size(0)==self.seq_len

    return{
        "encoder_input":encoder_input,
        "decoder_input":decoder_input,
        'label':label,
         "src_text":src_text,
        "tgt_text":tgt_text
    }




In [136]:
from pathlib import Path
def get_config():
    return{
        "batch_size": 6,
        "num_epochs": 20,
        "lr": 10**-4,
        "seq_len": 350,
        "d_model": 512,
        "lang_src": "en",
        "lang_tgt":"it",
        "model_folder": "weights",
        "model_filename": "tmodel_",
        "preload": None,
        "tokenizer_file":"tokenizer_{0}.json",
        "experiment_name":"runs/tmodel"


    }

def get_weights_file_path(config,epoch):
    model_folder= config["model_folder"]
    model_basename= config["model_base"]
    model_filename= f"{model_basename}{epoch}.pt"
    return str (Path('.') / model_folder / model_filename)




In [137]:
device =torch.device("cuda")
train_dataloader,val_dataloader,tokenizer_src,tokenizer_tgt = get_ds(get_config())
src_vocab_size = tokenizer_src.get_vocab_size()
tgt_vocab_size = tokenizer_tgt.get_vocab_size()
print(tgt_vocab_size)
d_model = 512
num_heads = 8
num_layers = 6
d_ff = 2048
max_seq_length = 350
dropout = 0.1


transformer = Transformer(src_vocab_size, tgt_vocab_size, d_model, num_heads, num_layers, d_ff, max_seq_length, dropout).to(device)

# for p in transformer.parameters():
#   if p.dim()>1:
#     nn.init.xavier_uniform_(p)

# for batch in batch_iterator:
#    enc_input= batch["encoder_input"].to(device) #(B,s)
#    dec_input= batch["decoder_input"].to(device)
#   #  enc_mask=batch["encoder_mask"].to(device) #(B,1,1,s)
#   #  dec_mask= batch["decoder_mask"].to(device) #(B,1,s,s)

#   #  enc_output=model.encode(enc_input,enc_mask)
#   #  dec_output=model.decode(enc_output,enc_mask,dec_input,dec_mask)
#   #  proj_output=model.project(dec_output) #(B,S,TGT_VOCAB_SIZE)

#             label=batch["label"].to(device) #(B,s)
#             loss=loss_fn(proj_output.view(-1,tokenizer_tgt.get_vocab_size()),label.view(-1))
#             batch_iterator.set_postfix({f"loss": f"{loss.item():6.3f}"})

#             loss.backward()
#             optimizer.step()
#             optimizer.zero_grad()
#             global_step+=1
#         model_filename=get_weights_file_path(config, f"{e:02d}")
#         torch.save({
#             "epoch":e,
#             "model_state_dict":model.state_dict(),
#             "optimizer_state_dict" : optimizer.state_dict(),
#             "global_step":global_step
#         }, model_filename)

# Generate random sample data
# src_data = torch.randint(1, src_vocab_size, (6, max_seq_length))  # (batch_size, seq_length)
# tgt_data = torch.randint(1, tgt_vocab_size, (6, max_seq_length))  # (batch_size, seq_length)

22463


In [138]:


criterion = nn.CrossEntropyLoss(ignore_index=tokenizer_src.token_to_id('[PAD]'),label_smoothing=0.1).to(device)
optimizer = optim.Adam(transformer.parameters(), lr=0.0001, betas=(0.9, 0.98), eps=1e-9)

transformer.train()

for epoch in range(50):
    batch_iterator=tqdm(train_dataloader, desc=f"Processing epoch {epoch:02d}")
    for batch in batch_iterator:
      optimizer.zero_grad()

      output = transformer(batch["encoder_input"].to(device), batch["decoder_input"].to(device))

      loss = criterion(output.view(-1, tgt_vocab_size), batch["label"].view(-1).to(device))
      loss.backward()
      optimizer.step()
      print(f"Epoch: {epoch+1}, Loss: {loss.item()}")
    torch.save(transformer.state_dict(),"model.pth")

Processing epoch 00:   0%|          | 1/4850 [00:00<27:17,  2.96it/s]

Epoch: 1, Loss: 10.192648887634277


Processing epoch 00:   0%|          | 2/4850 [00:00<23:39,  3.42it/s]

Epoch: 1, Loss: 10.057942390441895


Processing epoch 00:   0%|          | 3/4850 [00:00<23:07,  3.49it/s]

...

Processing epoch 02:   1%|          | 56/4850 [00:16<23:13,  3.44it/s]

Epoch: 3, Loss: 2.3700385093688965


Processing epoch 02:   1%|          | 57/4850 [00:16<23:17,  3.43it/s]

Epoch: 3, Loss: 2.277560234069824


KeyboardInterrupt: 

In [141]:
def validate(transformer, criterion, val_dataloader, tokenizer_src, tokenizer_tgt):
    transformer.eval()  # switch to evaluation mode
    transformer.load_state_dict(torch.load("model.pth"))
    total_loss = 0.0
    total_correct = 0
    total_predictions = 0

    with torch.no_grad():
        for batch in val_dataloader:
            encoder_input = batch["encoder_input"].to(device)
            decoder_input = batch["decoder_input"].to(device)
            labels = batch["label"].to(device)

            output = transformer(encoder_input, decoder_input)
            loss = criterion(output.view(-1, tgt_vocab_size), labels.view(-1))
            total_loss += loss.item()

            # Decode target, expected, and predicted sequences
            decoded_target = decode_sequence(labels, tokenizer_tgt)
            decoded_expected = decode_sequence(batch["label"], tokenizer_tgt)
            _, predicted = torch.max(output, 2)
            decoded_predicted = decode_sequence(predicted, tokenizer_tgt)
            source_input = decode_sequence(batch["encoder_input"], tokenizer_src)
            # Print target, expected, and predicted sequences
            print("Source:", source_input)
            print("Target:", decoded_target)
            print("Expected:", decoded_expected)
            print("Predicted:", decoded_predicted)
            print("***********************")

            # Calculate accuracy
            correct = ((predicted == labels) & (labels != tokenizer_tgt.token_to_id('[PAD]'))).sum().item()
            total_correct += correct
            total_predictions += labels.size(0) * labels.size(1)

    avg_loss = total_loss / len(val_dataloader)
    accuracy = total_correct / total_predictions

    print(f"Validation Loss: {avg_loss}, Accuracy: {accuracy}")

def decode_sequence(sequence, tokenizer):
    decoded_sequence = []
    for token in sequence.view(-1):
        token = token.item()
        if token == tokenizer.token_to_id('[PAD]'):
            break
        decoded_token = tokenizer.id_to_token(token)
        decoded_sequence.append(decoded_token)
    return " ".join(decoded_sequence)

# Usage example:
# Assuming you have `val_dataloader`, `tokenizer_src`, `tokenizer_tgt`, and `tgt_vocab_size` defined
# before and `criterion` defined as in your training loop
validate(transformer, criterion, val_dataloader, tokenizer_src, tokenizer_tgt)


Source: [SOS] " Not at all : they are full of jests and gaiety ." [EOS]
Target: — No davvero , sono anzi [UNK] . [EOS]
Expected: — No davvero , sono anzi [UNK] . [EOS]
Predicted: — No davvero , sono anzi [UNK] . [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [EOS] [E

KeyboardInterrupt: 